In [42]:
# noexport

!typech evaluation_utils_extended.ipynb

[NbConvertApp] Converting notebook evaluation_utils_extended.ipynb to python


In [1]:
from evaluation_utils import *

/usr/local/lib/python3.7/site-packages/getsecret/__init__.py:7: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  secrets = yaml.load(open('.getsecret.yaml'))
/usr/local/lib/python3.7/site-packages/getsecret/__init__.py:7: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  secrets = yaml.load(open('.getsecret.yaml'))


/usr/local/lib/python3.7/site-packages/getsecret/__init__.py:7: YAMLLoadWarning:

calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.



In [2]:
def get_difficulty_first_chosen_by_user(user):
  user_to_features_data = get_all_features_data()
  features_data = user_to_features_data.get(user, None)
  if features_data == None:
    return 'nothing'
  if len(features_data['difficulty_items']) == 0:
    return 'nothing'
  return features_data['difficulty_items'][0]['difficulty']

In [3]:
def get_difficulty_chosen_by_user_at_idx(user, idx):
  user_to_features_data = get_all_features_data()
  features_data = user_to_features_data.get(user, None)
  if features_data == None:
    return 'nothing'
  return features_data['difficulty_items'][idx]['difficulty']


In [4]:


def get_initial_difficulty_v2(tensor, parameter_info_list):
  feature = tensor['feature']
  history_length = feature.size()[0]
  timestep = 0
  #if len(feature) < 2:
  #  return 'nothing'
  enabled_feature_list = get_enabled_features_list_from_parameter_info_list(parameter_info_list)
  get_feature_index = make_get_index(enabled_feature_list)
  difficulty_feature_idx = get_feature_index('initial_difficulty')
  for difficulty_idx,difficulty in enumerate(['nothing', 'easy', 'medium', 'hard']):
    if feature[timestep][0][difficulty_feature_idx + difficulty_idx].item() > 0:
      return difficulty
  return 'nothing'

def get_first_chosen_difficulty_v2(tensor, parameter_info_list):
  user = tensor['user']
  feature = tensor['feature']
  history_length = feature.size()[0]
  if history_length < 2:
    return 'nothing'
  return get_difficulty_first_chosen_by_user(user)

def always_predict_most_common_previous_v2(tensor, parameter_info_list):
  feature = tensor['feature']
  history_length = feature.size()[0]
  if len(feature) < 2:
    return 'nothing'
  enabled_feature_list = get_enabled_features_list_from_parameter_info_list(parameter_info_list)
  get_feature_index = make_get_index(enabled_feature_list)
  difficulty_feature_idx = get_feature_index('difficulty')
  difficulty_choices = Counter()
  for timestep in range(0, history_length - 1):
    for difficulty_idx,difficulty in enumerate(['nothing', 'easy', 'medium', 'hard']):
      if feature[timestep][0][difficulty_feature_idx + difficulty_idx].item() > 0:
        difficulty_choices[difficulty] += 1
  output = most_common_key_for_counter(difficulty_choices)
  if output == None:
    return 'nothing'
  return output
  #return 'nothing'

In [5]:
def evaluate_function_model_on_dataset_v2(parameter_info_list, func, dataset, prefix='dev_') -> Dict[str, Any]:
  confusion = [[0,0,0,0],[0,0,0,0],[0,0,0,0],[0,0,0,0]]
  correct = 0
  total = 0
  for item in dataset:
    category_tensor = item['category']
    feature_tensor = item['feature']
    #if feature_tensor.size()[0] == 0:
    #    continue
    difficulty = tensor_to_difficulty(category_tensor)
    difficulty_idx = get_difficulty_idx(difficulty)
    #predicted_tensor = make_prediction(model, feature_tensor.cuda())
    #predicted_difficulty = prediction_to_difficulty(predicted_tensor)
    predicted_difficulty = func(item, parameter_info_list)
    predicted_difficulty_idx = get_difficulty_idx(predicted_difficulty)
    if predicted_difficulty_idx == difficulty_idx:
      correct += 1
    total += 1
    confusion[difficulty_idx][predicted_difficulty_idx] += 1
  return {
    prefix + 'correct': correct,
    prefix + 'total': total,
    prefix + 'confusion': confusion,
  }

In [6]:
def get_baseline_names():
  return [
    'initial_difficulty',
    'first_chosen',
    'always_nothing',
    'most_common_previous',
  ]

@jsonmemo1arg
def get_evaluation_results_for_named_baseline_v4(baseline_name):
  baseline_name_to_func = {
    'initial_difficulty': get_initial_difficulty_v2,
    'first_chosen': get_first_chosen_difficulty_v2,
    'always_nothing': always_predict_nothing,
    'most_common_previous': always_predict_most_common_previous_v2,
  }
  true = True
  false = False
  parameter_info_list : List[Dict[str, Any]] = get_default_parameter_info_list()
  #train_data,dev_data,test_data = get_data_for_parameters(parameter_info_list)
  baseline_func = baseline_name_to_func[baseline_name]
  return evaluate_function_model_on_dataset_v2(parameter_info_list, baseline_func, dev_data)

In [34]:
def get_default_parameter_info_list():
  true = True
  false = False
  return [{"name": "dataset_name", "type": "dataset", "values": ["2019_04_11"], "value": "2019_04_11"}, {"name": "model_name", "type": "model", "values": ["selfattentionlstm"], "value": "selfattentionlstm"}, {"name": "criterion", "type": "model", "values": ["NLLLoss"], "value": "NLLLoss"}, {"name": "learning_rate", "type": "model", "values": [0.005, 0.05, 0.0005, 5e-05], "value": 5e-05}, {"name": "window_embed_size", "type": "model", "values": [64, 128, 256, 512], "value": 256}, {"name": "difficulty", "type": "feature", "values": [true, false], "value": true}, {"name": "time_of_day", "type": "feature", "values": [true, false], "value": true}, {"name": "day_of_week", "type": "feature", "values": [true, false], "value": true}, {"name": "domain_productivity", "type": "feature", "values": [true, false], "value": true}, {"name": "domain_category", "type": "feature", "values": [true, false], "value": true}, {"name": "initial_difficulty", "type": "feature", "values": [true, false], "value": true}, {"name": "languages", "type": "feature", "values": [true, false], "value": true}, {"name": "num_prior_entries", "type": "dataparam", "values": [10, 20, 30, 40], "value": 10}, {"name": "sample_every_n_visits", "type": "dataparam", "values": [1], "value": 1}, {"name": "sample_difficulty_every_n_visits", "type": "dataparam", "values": [1], "value": 1}, {"name": "disable_prior_visit_history", "type": "dataparam", "values": [false, true], "value": false}, {"name": "disable_difficulty_history", "type": "dataparam", "values": [false, true], "value": false}, {"name": "enable_current_difficulty", "type": "dataparam", "values": [false, true], "value": false}, {"name": "num_features", "type": "model", "values": [277], "value": 277}]

@msgpackmemo
def get_default_train_dev_test_data():
  parameter_info_list = get_default_parameter_info_list()
  #set_parameter_in_parameter_info_list(parameter_info_list, 'sample_every_n_visits', 1)
  train_data,dev_data,test_data = get_data_for_parameters(parameter_info_list)
  return train_data,dev_data,test_data


In [11]:
# noexport

#train_data,dev_data,test_data = get_default_train_dev_test_data()

In [ ]:
#print(type(train_data))
#print((train_data[0][list(train_data[0].keys())[0]]))
#pytorch_tensor = train_data[0]['feature']

In [ ]:
#pytorch_serialized = json.dumps(pytorch_tensor.numpy().tolist())

In [ ]:
#import numpy

In [ ]:
#pytorch_new = torch.tensor(numpy.array(json.loads(pytorch_serialized), dtype='float32'), dtype=torch.float32)

In [ ]:
#pytorch_new.numpy().dtype

In [ ]:
# print(type(pytorch_tensor))
# print(pytorch_tensor.type())
# print(pytorch_tensor.numpy().dtype == numpy.float32)

In [12]:
# noexport

#a = get_default_train_dev_test_data()

In [24]:
def get_nearest_visit_idx_for_sample_rate(visit_idx, sample_rate):
  num_visits_ago = visit_idx % sample_rate
  return visit_idx - num_visits_ago

In [30]:
@jsonmemo1arg
def get_evaluation_results_for_sample_every_n_visits_v3(sample_every_n_visits):
  true = True
  false = False
  def evaluation_func(tensor, parameter_info_list):
    user = tensor['user']
    visit_idx = tensor['visit_idx']
    if visit_idx < 1:
      return 'nothing'
    sampled_visit_idx = get_nearest_visit_idx_for_sample_rate(visit_idx - 1, sample_every_n_visits)
    return get_difficulty_chosen_by_user_at_idx(user, sampled_visit_idx)
  parameter_info_list = get_default_parameter_info_list()
  train_data,dev_data,test_data = get_default_train_dev_test_data()
  return evaluate_function_model_on_dataset_v2(parameter_info_list, evaluation_func, dev_data)
  

In [31]:
@jsonmemo1arg
def get_evaluation_results_for_sample_every_n_seconds_v2(sample_every_n_seconds):
  true = True
  false = False
  user_to_idx_to_difficulty = {}
  def evaluation_func(tensor, parameter_info_list):
    user = tensor['user']
    visit_idx = tensor['visit_idx']
    if user not in user_to_idx_to_difficulty:
      user_to_idx_to_difficulty[user] = get_visit_idx_to_predictions_for_timed_sampling_rate(user, sample_every_n_seconds)
    #if visit_idx < 1:
    #  return 'nothing'
    #sampled_visit_idx = get_nearest_visit_idx_for_sample_rate(visit_idx - 1, sample_every_n_visits)
    return user_to_idx_to_difficulty[user][visit_idx]
  parameter_info_list = get_default_parameter_info_list()
  train_data,dev_data,test_data = get_default_train_dev_test_data()
  return evaluate_function_model_on_dataset_v2(parameter_info_list, evaluation_func, dev_data)
  

In [ ]:
@jsonmemo1arg
def get_evaluation_results_for_sample_every_n_seconds_v3(sample_every_n_seconds):
  true = True
  false = False
  user_to_idx_to_difficulty = {}
  def evaluation_func(tensor, parameter_info_list):
    user = tensor['user']
    visit_idx = tensor['visit_idx']
    if user not in user_to_idx_to_difficulty:
      user_to_idx_to_difficulty[user] = get_visit_idx_to_predictions_for_timed_sampling_rate_v2(user, sample_every_n_seconds)
    #if visit_idx < 1:
    #  return 'nothing'
    #sampled_visit_idx = get_nearest_visit_idx_for_sample_rate(visit_idx - 1, sample_every_n_visits)
    return user_to_idx_to_difficulty[user][visit_idx]
  parameter_info_list = get_default_parameter_info_list()
  train_data,dev_data,test_data = get_default_train_dev_test_data()
  return evaluate_function_model_on_dataset_v2(parameter_info_list, evaluation_func, dev_data)
  

In [ ]:
def get_visit_idx_to_predictions_for_timed_sampling_rate_v2(user, sampling_rate_seconds):
  user_to_features_data = get_all_features_data()
  features_data = user_to_features_data.get(user, None)
  if features_data == None:
    return 'nothing'
  sampled_according_to_time = []
  last_sampled_time = None
  last_sampled_value = 'nothing'
  for idx,item in enumerate(features_data['difficulty_items']):
    difficulty = item['difficulty']
    arrow_time = item['arrow_time']
    sampled_according_to_time.append(last_sampled_value)
    if last_sampled_time != None:
      seconds_since_last_sample = (arrow_time - last_sampled_time).total_seconds()
      if seconds_since_last_sample >= sampling_rate_seconds:
        last_sampled_time = arrow_time
        last_sampled_value = difficulty
    else:
      last_sampled_time = arrow_time
      last_sampled_value = difficulty
  return sampled_according_to_time


In [27]:
def get_visit_idx_to_predictions_for_timed_sampling_rate(user, sampling_rate_seconds):
  user_to_features_data = get_all_features_data()
  features_data = user_to_features_data.get(user, None)
  if features_data == None:
    return 'nothing'
  sampled_according_to_time = []
  last_sampled_time = None
  last_sampled_value = 'nothing'
  for idx,item in enumerate(features_data['difficulty_items']):
    difficulty = item['difficulty']
    arrow_time = item['arrow_time']
    sampled_according_to_time.append(last_sampled_value)
    if last_sampled_time != None:
      seconds_since_last_sample = (arrow_time - last_sampled_time).total_seconds()
      if seconds_since_last_sample >= sampling_rate_seconds:
        last_sampled_time = arrow_time
        last_sampled_value = difficulty
    else:
      last_sampled_time = arrow_time
      last_sampled_value = difficulty
  return sampled_according_to_time


In [28]:
def main():
  for baseline_name in ['initial_difficulty', 'first_chosen', 'always_nothing', 'most_common_previous']:
    print(baseline_name)
    print(get_evaluation_results_for_named_baseline_v4(baseline_name))
  
  sample_every_n_visits_options = [1,2,3,4,5,7,9,10,15,20,25,30,35,40,45,50,55,60,65,70,75,80,85,90,95,100,105,110,115,120,125,130]
  sample_every_n_visits_options.extend(list(range(1, 1000)))
  for sample_every_n_visits in sample_every_n_visits_options:
    print(sample_every_n_visits)
    print(get_evaluation_results_for_sample_every_n_visits_v3(sample_every_n_visits))


In [35]:
# noexport

main()

initial_difficulty
{'dev_correct': 2454, 'dev_total': 7560, 'dev_confusion': [[141, 1485, 810, 783], [281, 1183, 573, 160], [68, 575, 1079, 59], [4, 124, 184, 51]]}
first_chosen
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
always_nothing
{'dev_correct': 3219, 'dev_total': 7560, 'dev_confusion': [[3219, 0, 0, 0], [2197, 0, 0, 0], [1781, 0, 0, 0], [363, 0, 0, 0]]}
most_common_previous
{'dev_correct': 6552, 'dev_total': 7560, 'dev_confusion': [[2916, 213, 47, 43], [212, 1812, 147, 26], [85, 100, 1578, 18], [46, 20, 51, 246]]}
1
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/1.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/1.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/1.json for arg 1
done with computation 2019_04_25/get_evaluation_

done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/40.json
{'dev_correct': 5323, 'dev_total': 7560, 'dev_confusion': [[2097, 716, 146, 260], [275, 1563, 250, 109], [114, 188, 1461, 18], [49, 22, 90, 202]]}
45
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/45.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/45.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/45.json for arg 45
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/45.json
{'dev_correct': 5383, 'dev_total': 7560, 'dev_confusion': [[2146, 619, 167, 287], [238, 1554, 289, 116], [119, 196, 1447, 19], [49, 23, 55, 236]]}
50
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/50.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_ever

done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/120.json
{'dev_correct': 4549, 'dev_total': 7560, 'dev_confusion': [[1579, 962, 236, 442], [223, 1520, 319, 135], [131, 348, 1283, 19], [46, 24, 126, 167]]}
125
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/125.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/125.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/125.json for arg 125
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/125.json
{'dev_correct': 4523, 'dev_total': 7560, 'dev_confusion': [[1559, 977, 241, 442], [223, 1517, 322, 135], [131, 351, 1280, 19], [46, 24, 126, 167]]}
130
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/130.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_

done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/21.json
{'dev_correct': 5851, 'dev_total': 7560, 'dev_confusion': [[2497, 470, 93, 159], [256, 1656, 197, 88], [104, 169, 1455, 53], [46, 13, 61, 243]]}
22
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/22.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/22.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/22.json for arg 22
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/22.json
{'dev_correct': 5830, 'dev_total': 7560, 'dev_confusion': [[2483, 476, 95, 165], [249, 1649, 233, 66], [108, 158, 1440, 75], [48, 22, 35, 258]]}
23
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/23.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_

done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/39.json
{'dev_correct': 5330, 'dev_total': 7560, 'dev_confusion': [[2188, 601, 174, 256], [276, 1569, 246, 106], [113, 280, 1330, 58], [49, 22, 49, 243]]}
40
{'dev_correct': 5323, 'dev_total': 7560, 'dev_confusion': [[2097, 716, 146, 260], [275, 1563, 250, 109], [114, 188, 1461, 18], [49, 22, 90, 202]]}
41
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/41.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/41.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/41.json for arg 41
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/41.json
{'dev_correct': 5362, 'dev_total': 7560, 'dev_confusion': [[2166, 642, 146, 265], [232, 1595, 259, 111], [115, 287, 1361, 18], [49, 25, 49, 240]]}
42
exception in jsonmemo1arg for file 2019_04_

...

{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
929
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/929.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/929.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/929.json for arg 929
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/929.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
930
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/930.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/930.json'
performing computation 2019_04_25/get_evaluation_results_

done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/943.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
944
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/944.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/944.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/944.json for arg 944
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/944.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
945
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/945.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_fo

done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/959.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
960
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/960.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/960.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/960.json for arg 960
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/960.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
961
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/961.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_fo

done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/976.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
977
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/977.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/977.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/977.json for arg 977
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/977.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
978
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/978.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_fo

done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/993.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
994
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/994.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/994.json'
performing computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/994.json for arg 994
done with computation 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/994.json
{'dev_correct': 4069, 'dev_total': 7560, 'dev_confusion': [[1266, 1190, 321, 442], [223, 1506, 333, 135], [131, 501, 1130, 19], [46, 29, 121, 167]]}
995
exception in jsonmemo1arg for file 2019_04_25/get_evaluation_results_for_sample_every_n_visits_v3/995.json
[Errno 2] No such file or directory: '2019_04_25/get_evaluation_results_fo

In [36]:
# noexport

import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

baseline_name_and_correctness : List[Tuple[str, float]] = []
for baseline_name in get_baseline_names():
  results = get_evaluation_results_for_named_baseline_v4(baseline_name)
  correctness : float = float(results['dev_correct'] / results['dev_total'])
  baseline_name_and_correctness.append((baseline_name, correctness))

print(baseline_name_and_correctness)

[('initial_difficulty', 0.3246031746031746), ('first_chosen', 0.5382275132275133), ('always_nothing', 0.4257936507936508), ('most_common_previous', 0.8666666666666667)]


In [ ]:
# scatterplot = []
# for sample_every_n_visits in range(1, 200):
#   results = get_evaluation_results_for_sample_every_n_visits_v3(sample_every_n_visits)
#   scatterplot.append([sample_every_n_visits, results['dev_correct'] / results['dev_total']])




# # Create a trace
# trace = go.Scatter(
#     x = [x[0] for x in scatterplot],
#     y = [x[1] for x in scatterplot],
#     mode = 'markers'
# )

# data = [trace]

# # Plot and embed in ipython notebook!
# iplot(data)


In [39]:
# noexport

scatterplot = []
for n_seconds in range(1, 60*60*24*60, 60): # 60*60*24*60
  results = get_evaluation_results_for_sample_every_n_seconds_v2(n_seconds)
  scatterplot.append([n_seconds / 3600, results['dev_correct'] / results['dev_total']])




# Create a trace
trace = go.Scatter(
    x = [x[0] for x in scatterplot],
    y = [x[1] for x in scatterplot],
    mode = 'markers'
)

data = [trace]

# Plot and embed in ipython notebook!
iplot(data)
